In [639]:
import pandas as pd 
import numpy as np
import plotly.express as px
import matplotlib.pyplot as plt
import re
import json 
import geopandas as gpd
import  geoplot as  gplt
import geoplot.crs as gcrs
from shapely.geometry import Point
import shapely.wkt
import json
import geopandas
import plotly.graph_objs as go
from bs4 import BeautifulSoup
import requests
plt.style.use('ggplot')
pd.set_option('max_columns',30)

### Part1 data loading and clearning

In [640]:
df = pd.read_csv('../archive-5/business-licences_2013_2023.csv',delimiter=';')
df2 = pd.read_csv('../archive-5/business-licences-1997-to-2012.csv',delimiter=';')
df = pd.concat([df,df2])

/Users/sasha/opt/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3331: DtypeWarning:

Columns (13) have mixed types.Specify dtype option on import or set low_memory=False.



In [641]:
df.head()

FOLDERYEAR  LicenceRSN LicenceNumber  LicenceRevisionNumber  \
0        22.0     3912118     22-312284                    0.0   
1        22.0     3913006     22-101049                    0.0   
2        22.0     3914706     22-102749                    0.0   
3        22.0     3918590     22-106633                    0.0   
4        22.0     3918655     22-106698                    0.0   

                                  BusinessName       BusinessTradeName  \
0                       Madrona Fine Homes Inc                     NaN   
1                       1915 Haro Holdings Ltd                     NaN   
2                                SteamWipe Ltd                     NaN   
3  Richard Charles Hatchman (Richard Hatchman)  Doggone Smart Training   
4                  Ritz Wildlife Solutions Inc                     NaN   

   Status                 IssuedDate ExpiredDate     BusinessType  \
0  Issued  2022-04-21T15:42:49-07:00  2022-12-31       Contractor   
1  Issued  2021-12-14T15:47:22-08:00  2022-12-31  Apartment House   
2  Issued  2022-03-25T07:27:53-07:00  2022-12-31   Auto Detailing   
3  Issued  2021-12-09T11:33:52-08:00  2022-12-31  Animal Services   
4  Issued  2021-12-28T07:50:21-08:00  2022-12-31  Animal Services   

   BusinessSubType Unit UnitType   House   Street          City Province  \
0         Building  NaN      NaN     NaN      NaN  Bowen Island       BC   
1              NaN  NaN      NaN  1915.0  Haro St     Vancouver       BC   
2              NaN  NaN      NaN     NaN      NaN        Surrey       BC   
3  Animal Training  NaN      NaN     NaN      NaN         Delta       BC   
4   Animal Control  NaN      NaN     NaN      NaN     Coquitlam       BC   

  Country PostalCode LocalArea  NumberofEmployees  FeePaid  \
0      CA        NaN       NaN                0.0    243.0   
1      CA    V6G 1H9  West End                0.0  11520.0   
2      CA        NaN       NaN                2.0    163.0   
3      CA        NaN       NaN                1.0    163.0   
4      CA        NaN       NaN                1.0    163.0   

                 ExtractDate Geom  
0  2023-01-01T00:09:06-08:00  NaN  
1  2023-01-01T00:09:06-08:00  NaN  
2  2023-01-01T00:09:06-08:00  NaN  
3  2023-01-01T00:09:06-08:00  NaN  
4  2023-01-01T00:09:06-08:00  NaN

In [642]:
df.columns

Index(['FOLDERYEAR', 'LicenceRSN', 'LicenceNumber', 'LicenceRevisionNumber',
       'BusinessName', 'BusinessTradeName', 'Status', 'IssuedDate',
       'ExpiredDate', 'BusinessType', 'BusinessSubType', 'Unit', 'UnitType',
       'House', 'Street', 'City', 'Province', 'Country', 'PostalCode',
       'LocalArea', 'NumberofEmployees', 'FeePaid', 'ExtractDate', 'Geom'],
      dtype='object')

In [643]:
df.describe()

FOLDERYEAR    LicenceRSN  LicenceRevisionNumber  NumberofEmployees  \
count  1.664354e+06  1.664355e+06           1.664352e+06       1.664355e+06   
mean   2.155171e+01  1.784498e+06           1.115389e-02       7.275187e+03   
std    2.808762e+01  1.255325e+06           1.093434e-01       6.628871e+06   
min    0.000000e+00  1.000000e+00           0.000000e+00       0.000000e+00   
25%    7.000000e+00  7.329005e+05           0.000000e+00       0.000000e+00   
50%    1.400000e+01  1.499892e+06           0.000000e+00       0.000000e+00   
75%    2.000000e+01  2.822992e+06           0.000000e+00       1.000000e+00   
max    9.900000e+01  4.220362e+06           4.000000e+00       6.047106e+09   

            FeePaid  
count  1.383387e+06  
mean   2.638804e+02  
std    8.101909e+02  
min   -1.624500e+03  
25%    9.300000e+01  
50%    1.280000e+02  
75%    1.740000e+02  
max    8.722800e+04

In [644]:
df.corr()

FOLDERYEAR  LicenceRSN  LicenceRevisionNumber  \
FOLDERYEAR               1.000000   -0.250915              -0.013869   
LicenceRSN              -0.250915    1.000000               0.106820   
LicenceRevisionNumber   -0.013869    0.106820               1.000000   
NumberofEmployees       -0.000275    0.000419              -0.000112   
FeePaid                 -0.021126    0.071313              -0.023559   

                       NumberofEmployees   FeePaid  
FOLDERYEAR                     -0.000275 -0.021126  
LicenceRSN                      0.000419  0.071313  
LicenceRevisionNumber          -0.000112 -0.023559  
NumberofEmployees               1.000000 -0.000166  
FeePaid                        -0.000166  1.000000

#### Step 1 Finding Area of interest, 
##### The data contains date when Business Licenses / permissions were published, is there any patterns that I can find from the information ?

##### To answer this question, I think I can split the date informations into mutiple variables such as year, month, day, hour etc.


In [645]:
df = df.drop_duplicates(subset=['LicenceNumber','LicenceRevisionNumber','BusinessName','Status'],keep='last')
## remove .0 from the column
df['House'] = df['House'].apply(lambda row: str(row).replace('.0',''))

In [646]:
def update_same_year_status(df):
   for i in reversed(range(1,5)):
      lisense_num = df[df['LicenceRevisionNumber'] == i]['LicenceNumber'].values
      is_in_df = df[df['LicenceNumber'].isin(lisense_num)]
      df = df.drop(is_in_df[ is_in_df['LicenceRevisionNumber'] < i].index)
   return df

### if there are revision in same licence number , we keep the row with latest ( higheest revision number) and drop others

In [647]:
df = update_same_year_status(df)
df = df.drop_duplicates('LicenceNumber',keep='last')

In [648]:
len(df)

1625633

In [649]:
### creating time reated new datetime columns 
### this method also works but takes  much more time 
##df.apply(lambda row: str(row['IssuedDate']).split('T')[0] ,axis=1) 
## year, month day
df['time_ymd'] = pd.to_datetime([date.split('T')[0] for date in df['IssuedDate'].astype('str') ])
### hour, minutes
df['time_hm'] = [date.split('T')[-1].split('-')[0] for date in df['IssuedDate'].astype('str') ] 
## year 
df['issued_year']  = pd.to_datetime([ date.split('T')[0].split('-')[0] for date in df['IssuedDate'].astype('str') ] )
## month
df['issued_month']  = [re.split('[0-9][0-9][0-9][0-9]-',date.split('T')[0])[-1].split('-')[0] for date in df['IssuedDate'].astype('str') ] 
## day 
df['issued_day']  = [ date.split('T')[0].split('-')[-1]  for date in df['IssuedDate'].astype('str') ]

#### I created year-month-day, hour-minutes,year,month,day variables. 
#### Let's plot the frequency of the each variables to find patterms.
#### Frequency means how many permissions were issued on the same date,year,month etc.

### Date

In [822]:
fig =  px.line(df[df['Status']=='Issued'].groupby('time_ymd').count()['LicenceNumber'],
      labels={
      "time_ymd": "year",
      "value": "count",
      })
fig.update_layout(title_text='Issued licences  <br><sup>from 1997 to 2023</sup>', title_x=0.5,showlegend=False)
fig.show()
### see some seasonal trend 
### how about time of day ?

##### As you can see, there is a seasonality in the plot. It looks like many Bus-license were issued between the end and the beginning of the year.
### let's plot yearly and monthly count.

In [823]:
fig = px.line(df[df['Status']=='Issued'].groupby('issued_year').count()['LicenceNumber'][1:-1],
   labels={
      "value": "count",
      },)
fig.update_layout(title_text='Issued licences per year <br><sup>from 1997 to 2022</sup>', title_x=0.5,showlegend=False)
fig.show()

In [825]:
fig = px.bar(df[df['Status']=='Issued'].groupby('issued_month')['issued_month'].count()[:-1],
   labels={
      "index": "month",
      "value": "count",
      },)
fig.update_layout(title_text='Issued licences per month', title_x=0.5,showlegend=False)
fig.show()

####  Daily count

In [710]:
fig = px.line(
df[df['Status']=='Issued'].groupby('issued_day')['issued_day'].count()[:-1],
   labels={
      "index": "day",
      "value": "count",
      }
)
fig.update_layout(title_text='Issued applications per day', title_x=0.5)
fig.show()

#### Hourly

In [883]:
unique_hour,hour_count = np.unique( round(df.dropna(subset=['time_hm'])['time_hm'] /  pd.Timedelta(hours=1),0),  return_counts=True)
fig = px.line(x=unique_hour[1:],y=hour_count[1:], 
   labels={
      "x": "hour",
      "y": "count",
      },
)
fig.update_layout(title_text='licences issued time(hour)', title_x=0.5)
fig.show()

#### This plot shows licences/permissions were issued during standard working hour (8am~6pm).
#### Assuming following thigs 
- Productivity of officers is highly correlated with the number of licences/permissions they issue
- Workers work between 8am~6pm and take a lunch break between 12~1pm.
##### It seems consistent with the productivity of standard office workers because the number increases throughout noon (the peak is between 10 am to 12 pm) but decreases during lunch break time. After the break, the number of applications issued increased from 1~3pm but kept decreasing again after 3 pm till the end of work time.

##### If the above two assumptions are valid, then it is possible to think officers of business licences work normally.

### Let's also plot proportion of application status 

In [827]:
count = df.groupby(by='Status')['Status'].count()
sum_count = count.sum()
status_proportion = (count/sum_count)*100
fig = px.pie(values= status_proportion,names=status_proportion.index,
)
fig.update_layout(title_text='Licence application status<br><sup>from 1997 to 2023</sup>', title_x=0.5)

In [828]:
### for every year 
prob_year_status = df[['Status','issued_year','LicenceNumber']].groupby(by=['issued_year','Status']).count()['LicenceNumber']  /  df[['Status','issued_year','LicenceNumber']].groupby(by='issued_year').count()['LicenceNumber']
prob_year_status  = pd.DataFrame(prob_year_status.reset_index())
prob_year_status['issued_year'] = pd.to_datetime(prob_year_status['issued_year'])
prob_year_status['LicenceNumber'] = prob_year_status['LicenceNumber'].copy()*100
fig = px.line(prob_year_status[prob_year_status['Status'] == 'Issued'][1:-1]
   ,x='issued_year',y='LicenceNumber',color='Status',
   title='Changes in percentage of issued business licences/permissions',
   labels={
      "LicenceNumber": "Issued rate(%)",
      },
   )
fig.update_layout(title_x=0.5)
fig.show()

#### I'm interested in yearly data because it shows some trend which is hard to undersand with intuitions such as labour productivty. 

In [656]:
non_active = df[(df['Status'] == 'Inactive') | (df['Status'] == 'Gone Out of Business')].drop_duplicates('BusinessName').dropna(subset=['IssuedDate'])
active = df[(df['Status'] == 'Issued')]

In [657]:
non_active =df[(df['Status'] == 'Inactive') | (df['Status'] == 'Gone Out of Business')].dropna(subset=['IssuedDate'])

In [829]:
correct_order =  list(range(96,100)) + list(range(0,24)) 
active_year_count = active.groupby('FOLDERYEAR')['LicenceRSN'].count().reindex(correct_order)
active_year_count.index = sorted(np.delete(df['issued_year'].unique(),2))
fig = px.line(active_year_count[1:-1],
   labels={
      "index": "year",
      "value": "count",
      },
)
fig.update_layout(title_text='Total number of issued business licences per year <br><sup>from 2012 to 2021</sup>', title_x=0.5)
fig.show()

In [753]:
print(f'Avg number of business licences issued is {round(active_year_count[1:-1].mean(),2)}')

Avg number of business licences issued is 48452.54


##### The plot shows interesting changes in the yearly changes in the number of licences issued; it seems like the average number is around 48~9k per year. We see a upward trend in 30 years but there are some fluctuations which are likely caused by changes in economic circumistances because there are drop in number of issued licenses for 2008. The year when economy had huge crisis.  Also, observed big drop in issued licesnes for 2020 and 2021 the time when businesses strongly affected by covid-19 pandemic.
#### Also, I will plot percentage changes each year.

In [830]:
correct_order =  list(range(96,100)) + list(range(0,24)) 
growth_rate = active.groupby('FOLDERYEAR')['LicenceRSN'].count().reindex(correct_order)
growth_rate  = round(growth_rate.pct_change()*100,2).drop([96,97,23])
growth_rate.index = pd.to_datetime(list(range(1996,2000)) + list(range(2000,2024)) ,format='%Y')[2:-1]
colors= np.array(['blue',]*len(growth_rate))
colors[ np.where(growth_rate < 0)[0]] = 'red'
text_positions = ['outside']*len(growth_rate)
fig = px.bar(growth_rate,
   color=colors,
   text = growth_rate.apply(lambda value: str(value)  + '%'),
   color_discrete_sequence=["red","blue"],
   labels={
      "index": "year",
      "value": "Growth rate compared with last year (%)",
      }
)
newnames = {'red':'Negative','blue':'Positive'}
fig.for_each_trace(lambda t: t.update(name = newnames[t.name]))
fig.update_traces(textposition=text_positions)
fig.update_layout(title_text=' Growth rate of issued business licences <br><sup>Compared with previous year</sup>', title_x=0.5)
fig.show()


#### The plot shows there are moderate flucuations between 2014~2017. Big Positive changes in 2018 and 2019, but a negative change in the number of licences issued was observed in 2020.
#### The huge drop might be correlated with Covid 19 Pandemic, which influenced the economy.
#### Therefore, I hypothesize that measurements of the economy are highly correlated with changes in the number of licences issued because if the economy is good, people want to start their businesses. However, the number drops under recession because many companies will shut down under such circumstances, and future entrepreneurs might hesitate to start a business.

### To test my hypothesis, I also want to plot percentage changes in number of business either closed or inactive but the data shows only 45000 business shut down in 25 years which sound unrealistically optimistic(low) and the plot is not consistent with economic  So, I will not use the variables unfortunetly

In [792]:
growth_rate_nonactive = non_active.groupby('FOLDERYEAR')['LicenceRSN'].count().reindex(correct_order)
growth_rate_nonactive  = round(growth_rate_nonactive.pct_change()*100,2).drop([96,97,23])
growth_rate_nonactive.index = pd.to_datetime(list(range(1996,2000)) + list(range(2000,2024)) ,format='%Y')[2:-1]
##colors = np.array(['blue',]*8)
##colors[ np.where(growth_rate_nonactive < 0)[0]] = 'red'
fig = px.bar(growth_rate_nonactive,
   ##color=colors,
   text = growth_rate_nonactive.apply(lambda value: str(value)  + '%'),
   labels={
      "FOLDERYEAR": "year",
      "value": "Growth rate compared with last year (%)",
      }
)
newnames = {'blue':'Positive','red':'Negative'}
## fig.for_each_trace(lambda t: t.update(name = newnames[t.name]))
fig.update_layout(title_text='Percentage changes in the number of businesses closed<br><sup>Compared with previous year</sup>', title_x=0.5)
fig.show()

#### The plot tells that there are some changes in,but shows there is a signifcant increase in number of business closed in 2021 compared with 2020.

#### It's a time to collect economic mesurements data from website. 
#### The mesurements which I will collect are GDP, GDP per capita, Inflation_rate, GNP and GNP per capita.

In [662]:
def std(value):
   return np.array((value - value.mean())/ np.std(value))
def get_data(url):
   doc = BeautifulSoup(requests.get(url).text,'html.parser')
   div = doc.findAll("div",{"class": "col-xs-6"})
   table = [str(row) for row in div]
   return pd.read_html(repr(table))[0]
def get_year_of_interest(data):
   new_data =data.iloc[:24,2].iloc[::-1].apply(lambda row: row.rstrip('%')).astype('float')
   new_data.index = data.iloc[:24,0].iloc[::-1]
   return new_data

In [793]:
inflation_df = get_data('https://www.macrotrends.net/countries/CAN/canada/inflation-rate-cpi')
gdp_rate_canada = get_data('https://www.macrotrends.net/countries/CAN/canada/gdp-growth-rate')
gdp_capita_rate_canada = get_data('https://www.macrotrends.net/countries/CAN/canada/gdp-per-capita')
gnp_rate_canada = get_data('https://www.macrotrends.net/countries/CAN/canada/gnp-gross-national-product')
gnp_capita_rate_canada = get_data('https://www.macrotrends.net/countries/CAN/canada/gni-per-capita')

gdp_annual_canada  = get_year_of_interest(gdp_rate_canada)
gdp_capita_canada =   get_year_of_interest(gdp_capita_rate_canada) 
inflation_canada =    get_year_of_interest(inflation_df) 

gnp_annual_rate_canada = gnp_rate_canada.iloc[1:24,3].iloc[::-1].apply(lambda row: row.rstrip('%')).astype('float')
gnp_annual_rate_canada.index = gnp_rate_canada.iloc[:24,0].iloc[::-1][:-1]
gnp_capita_rate_canada  =    get_year_of_interest(gnp_capita_rate_canada) 

In [794]:
std_gdp_growth_rate = std(gdp_annual_canada)
std_gdp_capita_rate_canada = std(gdp_capita_canada)
std_bl_growth_rate =  std(growth_rate)
std_inflation_rate = std(inflation_canada )
std_gnp_rate_canada = std(gnp_annual_rate_canada)
std_gnp_capita_rate_canada = std(gnp_capita_rate_canada)

In [876]:
df_rate = pd.concat([pd.DataFrame(std_gdp_growth_rate),pd.DataFrame(std_gdp_capita_rate_canada),
   pd.DataFrame(std_bl_growth_rate), pd.DataFrame(std_inflation_rate),
   pd.DataFrame(std_gnp_rate_canada),pd.DataFrame(std_gnp_capita_rate_canada)
   ],axis=1 
   ).iloc[:,:]
df_rate.columns = ['gdp_growth','gdp_growth_capita','bl_growth', 'inflation_rate','gnp_growth','gnp_growth_capita']
df_rate[['gdp_growth_shift','gdp_growth_capita_shift','inflation_rate_shift','gnp_growth_shift','gnp_growth_capita_shift']] =  df_rate[['gdp_growth','gdp_growth_capita','inflation_rate','gnp_growth','gnp_growth_capita']].shift(1)


In [881]:
fig = go.Figure(data=[go.Table(
    header=dict(values=df_rate.corr()['bl_growth'].index[:6],
                line_color='darkslategray',
                fill_color='lightskyblue',
                align='left'),
    cells=dict(values= np.round(df_rate.corr()['bl_growth'].values[:6],4), # 2nd column
               line_color='darkslategray',
               fill_color='lightcyan',
               align='left'))
])
fig.update_layout(width=1000, height=400)
fig.update_layout(title_text='Correlations between growth in yearly business licences issued numbers and economic measurements.', 
        title_x=0.5)
fig.show()

In [882]:
fig = go.Figure(data=[go.Table(
    header=dict(values=df_rate.corr()['bl_growth'].index[6:],
                line_color='darkslategray',
                fill_color='lightskyblue',
                align='left'),
    cells=dict(values= np.round(df_rate.corr()['bl_growth'].values[6:],4), # 2nd column
               line_color='darkslategray',
               fill_color='lightcyan',
               align='left'))
])
fig.update_layout(width=1000, height=400)
fig.update_layout(title_text='Correlations between growth in yearly business licences issued numbers and economic measurements.', 
        title_x=0.5)
fig.show()

#### Let's take a look at where businesses are located in vacnouver.
#### Financial business

In [669]:
cibics = ['CCEC Credit Union','CIBC Mellon Trust Company', 'CTBC Bank Corp (Canada)']
cwbs = ['Canadian Western Bank & Trust','Canadian Western Bank & Trust Company','Canadian Western Bank Financial Group']
ccss = ['Coast Capital Savings Federal Credit Union','Coast Captial Savings Credit Union']
gffs = ["Gulf And Fraser Fishermen's Credit Union","Gulf and Fraser Fishermen's Credit Union"]
tds = ['TD Bank Financial Group', 'TD Canada Trust']
tctcs = ['The Canada Trust Co Mortgage Company', 'The Canada Trust Co Mortgate Company']
tdbs = ['The Toronto-Dominion Bank Tower Branch Pac Centre','Toronto Dominion Bank']
update_list = ['Anthony Sylvan Green & Sarah Christie Hoffman', 'Bank of Nova Scotia - Trust Co','Canadian Imperial Bank of Commerce',
'HSBC Bank Canada Corporate Real Estate','Mega International Commercial Bank Co Ltd','National Bank of Canada','Royal Bank of Canada'
,cibics, cwbs,ccss,gffs,tds,tctcs,tdbs] 
for index,name in  enumerate(df['BusinessName'][df['BusinessType']== 'Financial Institution']):
    if name == 'Anthony Sylvan Green & Sarah Christie Hoffman':
        df.loc[df['BusinessName'] == name,'BusinessName'] = 'Anthony S Green & Sarah C Hoffman'
    elif name == 'Bank of Nova Scotia - Trust Co':
        df.loc[df['BusinessName'] == name ,'BusinessName'] = 'Bank Of Nova Scotia'
    elif name in cibics:
        df.loc[df['BusinessName'] == name,'BusinessName'] = 'CIBC'
    elif name in cwbs:
       df.loc[df['BusinessName'] == name,'BusinessName']  = 'Canadian Western Bank'
    elif name in ccss:
        df.loc[df['BusinessName'] == name,'BusinessName'] = 'Coast Capital Savings Credit Union'
    elif name in gffs:
        df.loc[df['BusinessName'] == name,'BusinessName'] =  "Gulf & Fraser Fishermen's Credit Union"
    elif name in tds:
        df.loc[df['BusinessName'] == name,'BusinessName'] =  'TD Bank'
    elif name in tctcs:
        df.loc[df['BusinessName'] == name,'BusinessName'] = 'The Canada Trust Co Mortgage Co'
    elif name == 'Canadian Imperial Bank of Commerce':
        df.loc[df['BusinessName'] == name,'BusinessName'] =  'Canadian Imperial Bank Of Commerce'
    elif name == 'HSBC Bank Canada Corporate Real Estate':
        df.loc[df['BusinessName'] == name,'BusinessName']  = 'HSBC Bank Canada'
    elif name == 'Mega International Commercial Bank Co Ltd':
        df.loc[df['BusinessName'] == name,'BusinessName'] =  'Mega International Commercial Bank (Canada)'
    elif name == 'National Bank of Canada':
        df.loc[df['BusinessName'] == name,'BusinessName']  = 'National Bank Of Canada'
    elif name == 'Royal Bank of Canada':
        df.loc[df['BusinessName'] == name,'BusinessName'] = 'Royal Bank Of Canada'
    elif name == tdbs:
        df.loc[df['BusinessName'] == name,'BusinessName'] = 'The Toronto Dominion Bank'
    else:
        None

KeyboardInterrupt: 

In [798]:
van_map = gpd.read_file("/Users/sasha/Vancouver_job_analysis/local-area-boundary/local-area-boundary.shp")
van_map = van_map.sort_values(by='name').reset_index(drop=True)

In [799]:
def plot_geo_map(van_map,business_type,html_file_name):
    category_df = df[df['BusinessType'] == business_type]
    category_df = category_df[category_df['issued_year'] == '2021-01-01']
    geom = category_df[['Geom','BusinessName','LocalArea']].drop_duplicates(subset=['Geom'])
    ## get only lat and lon tutde
    geo_points = [ json.loads(str(geo))['coordinates'] for geo in geom.dropna()['Geom'] ]
    geo_points = [Point(xy) for xy in geo_points]
    pd_mapset = gpd.GeoDataFrame(geometry = geo_points)
    pd_mapset['BusinessName'] = geom.dropna()['BusinessName'].values 
    pd_mapset['LocalArea'] = geom.dropna()['LocalArea'].values
    van_dist = geopandas.GeoDataFrame(van_map['geometry']).__geo_interface__
    not_on_list =   set(df['LocalArea'].dropna()) -  set(geom.dropna()['LocalArea'].values)
    zero_list= [[loc_name,0]  for loc_name in not_on_list ] 
    aa = pd_mapset.groupby(by='LocalArea',dropna=False).count() \
        .reset_index()[['LocalArea','BusinessName']].values.tolist()
    local_names =  sorted(zero_list + aa)
    van_map['finance_count']  = pd.DataFrame(local_names)[1]
    ##print(geo_points)
    fig = px.choropleth_mapbox(geojson=van_dist,
                           locations=van_map.index,
                           color=van_map['finance_count'],
                           color_continuous_scale="blues",
                           range_color=(0, 37),
                           mapbox_style="carto-positron",
                           zoom=10.5, 
                           center = {"lat": 49.241756, "lon": -123.112617},
                           opacity=0.7,
                           hover_name = local_names,
                           labels={'unemp':'unemployment rate'}
                          )
    ##fig.add_trace(
    ##    go.Scatter()
    ##)
    fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

    ##fig.write_html(f'../codes/{html_file_name}.html')
    return fig.show()

In [800]:
plot_geo_map(van_map, 'Financial Institution','a')